In [72]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
sns.set_theme(style="darkgrid")
from pandas_profiling import ProfileReport
import math
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.preprocessing import StandardScaler, LabelEncoder
from imblearn.under_sampling import RandomUnderSampler, NearMiss, OneSidedSelection
from imblearn.over_sampling import RandomOverSampler, SMOTE, BorderlineSMOTE
from collections import Counter
from sklearn.model_selection import GridSearchCV
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix
from pandas_profiling import ProfileReport
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from imblearn.over_sampling import SMOTE
from sklearn.svm import SVC
from sklearn import tree
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import GridSearchCV, cross_val_score
from sklearn.neural_network import MLPClassifier
from sklearn.gaussian_process.kernels import RBF
from sklearn.ensemble import AdaBoostClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.linear_model import SGDClassifier
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
from sklearn.model_selection import RepeatedStratifiedKFold
from sklearn.tree import DecisionTreeRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.linear_model import LogisticRegression
from sklearn import preprocessing
import xgboost as xgb
from matplotlib import pyplot
from numpy import mean

In [73]:
#realizando leitura dos datasets

base_train = pd.read_csv("data_orders_train.csv")
base_test = pd.read_csv("data_orders_test.csv")

In [74]:
#analise exploratoria do base Train
profile = ProfileReport(base_train)
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [75]:
#analise exploratorio da base de teste
profile_test = ProfileReport(base_test)
profile_test

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [76]:
#visualisando os dados nulos
base_train.isnull().sum()

category                           0
price                              0
freight_value                      0
customer_lat                      25
customer_lng                      25
seller_lat                         6
seller_lng                         6
order_status                       0
order_approved_at                  0
order_delivered_customer_date    147
dtype: int64

In [77]:
#removendo os dados nulos da base de dadso
base_train = base_train.dropna()
base_test = base_test.dropna()


In [78]:
#verificandos os dados nulos
base_test.isnull().sum()

category                         0
price                            0
freight_value                    0
customer_lat                     0
customer_lng                     0
seller_lat                       0
seller_lng                       0
order_status                     0
order_approved_at                0
order_delivered_customer_date    0
dtype: int64

In [79]:
#verificandos os dados nulos
base_train.isnull().sum()

category                         0
price                            0
freight_value                    0
customer_lat                     0
customer_lng                     0
seller_lat                       0
seller_lng                       0
order_status                     0
order_approved_at                0
order_delivered_customer_date    0
dtype: int64

In [80]:
base_test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1952 entries, 0 to 1999
Data columns (total 10 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   category                       1952 non-null   object 
 1   price                          1952 non-null   float64
 2   freight_value                  1952 non-null   float64
 3   customer_lat                   1952 non-null   float64
 4   customer_lng                   1952 non-null   float64
 5   seller_lat                     1952 non-null   float64
 6   seller_lng                     1952 non-null   float64
 7   order_status                   1952 non-null   object 
 8   order_approved_at              1952 non-null   object 
 9   order_delivered_customer_date  1952 non-null   object 
dtypes: float64(6), object(4)
memory usage: 167.8+ KB


In [81]:
base_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7824 entries, 0 to 7999
Data columns (total 10 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   category                       7824 non-null   object 
 1   price                          7824 non-null   float64
 2   freight_value                  7824 non-null   float64
 3   customer_lat                   7824 non-null   float64
 4   customer_lng                   7824 non-null   float64
 5   seller_lat                     7824 non-null   float64
 6   seller_lng                     7824 non-null   float64
 7   order_status                   7824 non-null   object 
 8   order_approved_at              7824 non-null   object 
 9   order_delivered_customer_date  7824 non-null   object 
dtypes: float64(6), object(4)
memory usage: 672.4+ KB


In [82]:
#transformando a colunas pro tipo data

base_train["order_approved_at"] = pd.to_datetime(base_train["order_approved_at"])
base_train["order_delivered_customer_date"] = pd.to_datetime(base_train["order_delivered_customer_date"]) 

base_test["order_approved_at"] = pd.to_datetime(base_test["order_approved_at"])
base_test["order_delivered_customer_date"] = pd.to_datetime(base_test["order_delivered_customer_date"]) 

C:\Users\tassi\AppData\Local\Temp\ipykernel_15396\407490679.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  base_train["order_approved_at"] = pd.to_datetime(base_train["order_approved_at"])
C:\Users\tassi\AppData\Local\Temp\ipykernel_15396\407490679.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  base_train["order_delivered_customer_date"] = pd.to_datetime(base_train["order_delivered_customer_date"])
C:\Users\tassi\AppData\Local\Temp\ipykernel_15396\407490679.py:6: SettingWithCopyWarning: 
A value i

In [83]:
display(base_test)

category   price  freight_value  customer_lat  \
0     informatica_acessorios   79.90          15.31    -29.166314   
1            cama_mesa_banho   39.99          18.23    -16.697612   
2              esporte_lazer   27.90          14.52    -23.571450   
3                  telefonia  779.00          27.38    -19.925110   
4              esporte_lazer   43.00          18.40    -31.757103   
...                      ...     ...            ...           ...   
1995            beleza_saude  287.70          24.94    -12.253483   
1996              automotivo   38.00          25.63    -29.738280   
1997                pet_shop   99.20          21.11    -22.325549   
1998         cama_mesa_banho   15.90          11.85    -22.692949   
1999           esporte_lazer   54.90          15.26    -30.090468   

      customer_lng  seller_lat  seller_lng order_status   order_approved_at  \
0       -51.178314  -23.413743  -51.907543    delivered 2017-09-26 17:26:24   
1       -49.275774  -21.757321  -48.829744    delivered 2018-03-15 12:49:18   
2       -46.647981  -23.390607  -51.446644    delivered 2017-03-07 11:55:15   
3       -44.259942  -23.770304  -53.293996    delivered 2018-08-16 10:10:26   
4       -52.317667  -24.008923  -46.419125    delivered 2018-06-23 13:40:01   
...            ...         ...         ...          ...                 ...   
1995    -38.951224  -23.571153  -46.620436    delivered 2018-05-02 20:38:42   
1996    -51.142599  -21.422173  -45.964344    delivered 2018-01-09 07:17:40   
1997    -49.094331  -22.729029  -47.641148    delivered 2018-04-13 17:55:13   
1998    -46.982878  -21.757321  -48.829744    delivered 2017-06-10 03:03:37   
1999    -51.235530  -25.528424  -49.275490    delivered 2018-05-08 04:33:58   

     order_delivered_customer_date  
0              2017-10-06 13:42:33  
1              2018-03-28 20:44:41  
2              2017-03-20 12:04:28  
3              2018-08-24 15:36:38  
4              2018-07-06 23:44:36  
...                            ...  
1995           2018-05-15 10:49:55  
1996           2018-01-22 21:08:58  
1997           2018-04-18 16:22:00  
1998           2017-06-22 14:08:44  
1999           2018-05-19 16:07:23  

[1952 rows x 10 columns]

In [84]:
display(base_train)

category  price  freight_value  customer_lat  \
0           moveis_decoracao   38.4          12.69    -21.191023   
1                 brinquedos   25.6          16.11    -22.876210   
2     informatica_acessorios  139.0          17.41    -12.975553   
3           moveis_decoracao   54.9          14.55    -28.038738   
4     informatica_acessorios  194.8          19.24    -26.890666   
...                      ...    ...            ...           ...   
7995           esporte_lazer    9.9           8.27    -23.652251   
7996            beleza_saude  440.0          11.44    -23.485397   
7997        moveis_decoracao  289.0          41.12    -29.706591   
7998           esporte_lazer   69.9          19.46    -21.201065   
7999  informatica_acessorios  175.5          16.99    -30.004097   

      customer_lng  seller_lat  seller_lng order_status   order_approved_at  \
0       -47.767914  -23.595499  -46.559727    delivered 2017-10-22 21:14:47   
1       -43.519817  -23.049552  -47.837621    delivered 2017-10-01 13:49:22   
2       -38.428999  -23.302318  -45.971888    delivered 2017-12-03 14:13:33   
3       -48.631463  -22.767878  -47.385501    delivered 2017-02-28 23:22:08   
4       -48.655328  -28.596704  -51.786946    delivered 2018-05-08 04:34:10   
...            ...         ...         ...          ...                 ...   
7995    -46.538344  -23.505548  -47.469705    delivered 2017-11-12 18:55:31   
7996    -46.809794  -22.726194  -47.337255    delivered 2018-04-16 08:00:38   
7997    -51.121924   -5.840248  -35.207931    delivered 2018-03-20 03:10:51   
7998    -47.802366  -29.190856  -51.230239    delivered 2018-04-01 23:15:16   
7999    -51.196319  -23.382472  -51.927966    delivered 2017-10-13 16:30:46   

     order_delivered_customer_date  
0              2017-10-31 14:55:49  
1              2017-11-20 11:38:22  
2              2017-12-28 22:33:08  
3              2017-03-13 12:38:30  
4              2018-05-14 18:52:56  
...                            ...  
7995           2017-11-21 22:18:02  
7996           2018-07-11 15:06:43  
7997           2018-04-25 13:05:17  
7998           2018-04-13 17:12:09  
7999           2017-10-26 17:45:31  

[7824 rows x 10 columns]

In [85]:
import datetime as dt

In [86]:
base_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7824 entries, 0 to 7999
Data columns (total 10 columns):
 #   Column                         Non-Null Count  Dtype         
---  ------                         --------------  -----         
 0   category                       7824 non-null   object        
 1   price                          7824 non-null   float64       
 2   freight_value                  7824 non-null   float64       
 3   customer_lat                   7824 non-null   float64       
 4   customer_lng                   7824 non-null   float64       
 5   seller_lat                     7824 non-null   float64       
 6   seller_lng                     7824 non-null   float64       
 7   order_status                   7824 non-null   object        
 8   order_approved_at              7824 non-null   datetime64[ns]
 9   order_delivered_customer_date  7824 non-null   datetime64[ns]
dtypes: datetime64[ns](2), float64(6), object(2)
memory usage: 672.4+ KB


In [87]:
#criando a coluna prazo de entrega para utilizando a as colunas que o produto saiu e que dia chegou ao lucal de destino
base_train["prazo_entrega"] = (base_train['order_delivered_customer_date'] - base_train['order_approved_at']).dt.days


C:\Users\tassi\AppData\Local\Temp\ipykernel_15396\2779244665.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  base_train["prazo_entrega"] = (base_train['order_delivered_customer_date'] - base_train['order_approved_at']).dt.days


In [88]:
#modificando a coluna para trazer apenas a quantidade de dias
base_test["prazo_entrega"] = (base_test['order_delivered_customer_date'] - base_test['order_approved_at']).dt.days

C:\Users\tassi\AppData\Local\Temp\ipykernel_15396\147327697.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  base_test["prazo_entrega"] = (base_test['order_delivered_customer_date'] - base_test['order_approved_at']).dt.days


In [89]:
#funçao removida da internet
#objetivo tranforma latitude e longitude em distancia.

import pandas as pd
import numpy as np
from pyproj import Geod

wgs84_geod = Geod(ellps='WGS84') #Distance will be measured on this ellipsoid - more accurate than a spherical method

#Get distance between pairs of lat-lon points
def Distance(lat1,lon1,lat2,lon2):
  az12,az21,dist = wgs84_geod.inv(lon1,lat1,lon2,lat2) #Yes, this order is correct
  return dist

#Add/update a column to the data frame with the distances (in metres)
base_train['distancia_km'] = Distance(base_train['customer_lat'].tolist(),base_train['customer_lng'].tolist(),base_train['seller_lat'].tolist(),base_train['seller_lng'].tolist())
base_test['distancia_km'] = Distance(base_test['customer_lat'].tolist(),base_test['customer_lng'].tolist(),base_test['seller_lat'].tolist(),base_test['seller_lng'].tolist())



C:\Users\tassi\AppData\Local\Temp\ipykernel_15396\3956836388.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  base_train['distancia_km'] = Distance(base_train['customer_lat'].tolist(),base_train['customer_lng'].tolist(),base_train['seller_lat'].tolist(),base_train['seller_lng'].tolist())
C:\Users\tassi\AppData\Local\Temp\ipykernel_15396\3956836388.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  base_test['distancia_km'] = Distance(base_test['customer_lat'].tolist(),base_test['customer_lng'].tolist(

In [90]:
#relizando calculo para transforma para KM

base_test['distancia_km'] = base_test['distancia_km'] / 10000
base_train['distancia_km'] = base_train['distancia_km'] / 10000

C:\Users\tassi\AppData\Local\Temp\ipykernel_15396\1162481525.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  base_test['distancia_km'] = base_test['distancia_km'] / 10000
C:\Users\tassi\AppData\Local\Temp\ipykernel_15396\1162481525.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  base_train['distancia_km'] = base_train['distancia_km'] / 10000


In [91]:
#Criando coluna do mes do pedido.
base_train["order_approved_month"] = base_train["order_approved_at"].dt.month
base_test["order_approved_month"] = base_test["order_approved_at"].dt.month

C:\Users\tassi\AppData\Local\Temp\ipykernel_15396\4144512280.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  base_train["order_approved_month"] = base_train["order_approved_at"].dt.month
C:\Users\tassi\AppData\Local\Temp\ipykernel_15396\4144512280.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  base_test["order_approved_month"] = base_test["order_approved_at"].dt.month


In [92]:
base_train

category  price  freight_value  customer_lat  \
0           moveis_decoracao   38.4          12.69    -21.191023   
1                 brinquedos   25.6          16.11    -22.876210   
2     informatica_acessorios  139.0          17.41    -12.975553   
3           moveis_decoracao   54.9          14.55    -28.038738   
4     informatica_acessorios  194.8          19.24    -26.890666   
...                      ...    ...            ...           ...   
7995           esporte_lazer    9.9           8.27    -23.652251   
7996            beleza_saude  440.0          11.44    -23.485397   
7997        moveis_decoracao  289.0          41.12    -29.706591   
7998           esporte_lazer   69.9          19.46    -21.201065   
7999  informatica_acessorios  175.5          16.99    -30.004097   

      customer_lng  seller_lat  seller_lng order_status   order_approved_at  \
0       -47.767914  -23.595499  -46.559727    delivered 2017-10-22 21:14:47   
1       -43.519817  -23.049552  -47.837621    delivered 2017-10-01 13:49:22   
2       -38.428999  -23.302318  -45.971888    delivered 2017-12-03 14:13:33   
3       -48.631463  -22.767878  -47.385501    delivered 2017-02-28 23:22:08   
4       -48.655328  -28.596704  -51.786946    delivered 2018-05-08 04:34:10   
...            ...         ...         ...          ...                 ...   
7995    -46.538344  -23.505548  -47.469705    delivered 2017-11-12 18:55:31   
7996    -46.809794  -22.726194  -47.337255    delivered 2018-04-16 08:00:38   
7997    -51.121924   -5.840248  -35.207931    delivered 2018-03-20 03:10:51   
7998    -47.802366  -29.190856  -51.230239    delivered 2018-04-01 23:15:16   
7999    -51.196319  -23.382472  -51.927966    delivered 2017-10-13 16:30:46   

     order_delivered_customer_date  prazo_entrega  distancia_km  \
0              2017-10-31 14:55:49              8     29.388813   
1              2017-11-20 11:38:22             49     44.319294   
2              2017-12-28 22:33:08             25    139.328263   
3              2017-03-13 12:38:30             12     59.719386   
4              2018-05-14 18:52:56              6     36.201530   
...                            ...            ...           ...   
7995           2017-11-21 22:18:02              9      9.645156   
7996           2018-07-11 15:06:43             86      9.994401   
7997           2018-04-25 13:05:17             36    312.584493   
7998           2018-04-13 17:12:09             11     94.995400   
7999           2017-10-26 17:45:31             13     73.726996   

      order_approved_month  
0                       10  
1                       10  
2                       12  
3                        2  
4                        5  
...                    ...  
7995                    11  
7996                     4  
7997                     3  
7998                     4  
7999                    10  

[7824 rows x 13 columns]

In [93]:
# fazer X_treino  and X_test = preco, freight_value, trecho_km(criando) 
# fazer y_teste anda y_treino =  prazo_entrega
# pradronizar os dados SdandaScarle
# criar modelo de regreção linear multipla SKlearn
# achar o r2

In [94]:
#realizando separação da base de treino de base de teste

colunas = ['price', 'freight_value', 'customer_lat', 'customer_lng', 'seller_lat', 'seller_lng', 'order_approved_month', 'distancia_km']

X_treino = base_train.loc[:, colunas].values
y_treino = base_train.loc[:, 'prazo_entrega'].values

X_teste = base_test.loc[:, colunas].values
y_teste = base_test.loc[:, 'prazo_entrega'].values

In [95]:
print ('X_train: numero de linhas e colunas: {}'.format(X_treino.shape))
print ('X_test: numero de linhas e colunas: {}'.format(X_teste.shape))
print ('y_train: numero de linhas e colunas: {}'.format(y_treino.shape))
print ('y_test: numero de linhas e colunas: {}'.format(y_teste.shape))

X_train: numero de linhas e colunas: (7824, 8)
X_test: numero de linhas e colunas: (1952, 8)
y_train: numero de linhas e colunas: (7824,)
y_test: numero de linhas e colunas: (1952,)


In [96]:
#realizando normalizaçao da base de dados
sc =  preprocessing.StandardScaler()

X_treino = sc.fit_transform(X_treino)


X_teste = sc.transform(X_teste) 

In [97]:
#criando modelo

from sklearn.model_selection import train_test_split 
from sklearn.linear_model import LinearRegression
from sklearn import metrics

lr = LinearRegression(max_depth=27)

lr.fit(X_treino, y_treino)


TypeError: LinearRegression.__init__() got an unexpected keyword argument 'max_depth'

In [ ]:
#criando array com valores previsto
y_previsao = lr.predict(X_teste)
y_previsao


array([12.01371713, 11.47165257, 11.94646278, ...,  8.89617583,
        9.03852504, 11.42220572])

In [ ]:

#verificando R2
from sklearn.metrics import r2_score
# Score R2

score=r2_score(y_teste, y_previsao)

print('R2:  ',score)


R2:   0.2017315534208255


infelizmente não conseguir chegar ao R2 desejado para trabalho não conseguir arruma um forma subir o valor do R2

#### Mean Absolute Error (MAE) é a média do valor absoluto dos erros.

#### Erro Quadrático Médio (MSE) é a média dos erros quadráticos

#### Erro médio quadrático da raiz (RMSE) é a raiz quadrada da média dos erros quadráticos

In [ ]:
print('MAE:', metrics.mean_absolute_error(y_teste, y_pred))
print('MSE:', metrics.mean_squared_error(y_teste, y_pred))
print('RMSE:', np.sqrt(metrics.mean_squared_error(y_teste, y_pred)))

NameError: name 'y_pred' is not defined

In [ ]:
# Obtendo os resíduos
residuals = y_teste - y_pred
# Plotando o valor previsto x valor real, a relação entre os dois deve ser linear
# Para isso utilizaremos a biblioteca matplotlib
import matplotlib.pyplot as plt
%matplotlib inline
ax = plt.scatter(y_pred, y_teste)
ax.figure.set_size_inches(12, 6)
plt.title('Previsão x Real', fontdict={'fontsize': 16})
plt.xlabel('Previsão', fontdict={'fontsize': 16})
plt.ylabel('Real', fontdict={'fontsize': 16})
ax
# Importando o módulo metrics para as avaliações do modelo
import sklearn.metrics as metrics
# Mostrando o valor do R²
print('R² =', metrics.r2_score(y_true=y_teste, y_pred=y_pred))